In [1]:
import os
import tensorflow as tf

use_cpu = False

if use_cpu:
    os.environ['CUDA_VISIBLE_DEVICES'] = '-1'
    os.environ['CPU_ONLY'] = "TRUE"

    physical_devices = tf.config.list_physical_devices('CPU')

    tf.config.set_logical_device_configuration(
        physical_devices[0],
        [tf.config.LogicalDeviceConfiguration() for i in range(8)])
    logical_devices = tf.config.list_logical_devices('CPU')

    print(logical_devices)
else:
    os.environ['CPU_ONLY'] = "FALSE"
    physical_devices = tf.config.list_physical_devices('GPU')
    print(physical_devices)

[PhysicalDevice(name='/physical_device:GPU:0', device_type='GPU')]


In [2]:
from latentneural.data import DataManager
from latentneural import TNDM
from latentneural.runtime import Runtime, ModelType
from latentneural.utils import AdaptiveWeights


data_dir = os.path.join('..', '..', 'latentneural', 'data', 'storage', 'lorenz', '20210610T215300')
dataset, settings = DataManager.load_dataset(
    directory=data_dir,
    filename='dataset.h5')

In [3]:
print(settings)
print('\nDataset keys:', dataset.keys())

{'step': 0.01, 'stop': 1, 'neurons': 30, 'base_rate': 5, 'latent_dim': 3, 'relevant_dim': 2, 'behaviour_dim': 4, 'conditions': 1, 'trials': 100, 'initial_conditions': '<function uniform.<locals>.callable at 0x7f92b42ac940>', 'selected_condition': 0, 'seed': 12345, 'train_pct': 0.7, 'valid_pct': 0.1, 'test_pct': 0.2, 'created': '2021-06-10T21:56:46.415999'}

Dataset keys: dict_keys(['behaviour_weights', 'neural_weights', 'relevant_dims', 'test_behaviours', 'test_behaviours_noiseless', 'test_data', 'test_latent', 'test_rates', 'time_data', 'train_behaviours', 'train_behaviours_noiseless', 'train_data', 'train_latent', 'train_rates', 'valid_behaviours', 'valid_behaviours_noiseless', 'valid_data', 'valid_latent', 'valid_rates'])


In [4]:
neural_data = dataset['train_data'].astype('float')
valid_neural_data = dataset['valid_data'].astype('float')
behavioural_data = dataset['train_behaviours'].astype('float')
valid_behavioural_data = dataset['valid_behaviours'].astype('float')

In [5]:
from datetime import datetime
from collections import defaultdict
logdir = os.path.join(data_dir, 'results', 'tndm', datetime.now().strftime("%Y%m%d-%H%M%S"))

optimizer = tf.keras.optimizers.Adam(
    learning_rate=1e-2,
    beta_1=0.9, 
    beta_2=0.999,
    epsilon=1e-01)

layers_settings=defaultdict(lambda: dict(
    kernel_initializer=tf.keras.initializers.VarianceScaling(
        scale=1.0, mode='fan_in', distribution='normal'),
    kernel_regularizer=tf.keras.regularizers.l2(l=0.1)
))
layers_settings['encoder'].update(dict(dropout=0.05, var_min=0.1, var_max=0.1))
layers_settings['relevant_decoder'].update(dict(kernel_regularizer=tf.keras.regularizers.l2(l=1),
                                      recurrent_regularizer=tf.keras.regularizers.l2(l=1),
                                      original_cell=False))    
layers_settings['irrelevant_decoder'].update(dict(kernel_regularizer=tf.keras.regularizers.l2(l=1),
                                      recurrent_regularizer=tf.keras.regularizers.l2(l=1),
                                      original_cell=False))    
layers_settings['behavioural_dense'].update(dict(behaviour_type='synchronous',      
                                                behaviour_sigma=1))    
model, history = Runtime.train(
    model_type=ModelType.TNDM,
    adaptive_lr=dict(factor=0.95, patience=10, min_lr=1e-5),
    model_settings=dict(
        relevant_factors=2,
        irrelevant_factors=1,
        encoded_space=64,
        max_grad_norm=200,
        encoded_var_max=0.1,
        encoded_var_min=0.1,
        timestep=settings['step']
    ),
    layers_settings=layers_settings,
    optimizer=optimizer, 
    epochs=1000, 
    logdir=logdir,
    train_dataset=(neural_data, behavioural_data), 
    val_dataset=(valid_neural_data, valid_behavioural_data),
    adaptive_weights=AdaptiveWeights(
        initial=[1.0, 1.0, .0, .0, 1.0, .0],
        update_start=[0, 0, 1000, 1000, 0, 0],
        update_rate=[0., 0., 0.0005, 0.0005, 0.0, 0.0005],
        min_weight=[1.0, 1.0, 0.0, 0.0, 1.0, 0.0]
    ),
    batch_size=16
)

/home/alessandrofacchin/miniconda/envs/latentneural/lib/python3.8/site-packages/tensorflow/python/data/ops/dataset_ops.py:3703: UserWarning: Even though the `tf.config.experimental_run_functions_eagerly` option is set, this option does not apply to tf.data functions. To force eager execution of tf.data functions, please use `tf.data.experimental.enable.debug_mode()`.
  warnings.warn(


Epoch 1/1000
5/5 [==============================] - 3s 452ms/step - loss: 2935.6184 - loss/neural: 1785.2829 - loss/behavioural: 1230.3740 - loss/relevant_kldiv: 48.5635 - loss/irrelevant_kldiv: 48.4761 - loss/reg: 1936.7819 - weights/neural_loglike: 1.0000 - weights/behavioural_loglike: 1.0000 - weights/relevant_kldiv: 0.0000e+00 - weights/irrelevant_kldiv: 0.0000e+00 - weights/reg: 5.8333e-04 - learning_rate: 0.0100 - grads/EncoderGRUForward_grucell2: 19.1930 - grads/EncoderGRUBackward_grucell1: 18.9829 - grads/EncoderDense: 5088.5833 - grads/RelevantDenseMean: 21.7158 - grads/IrrelevantDenseMean: 13.0241 - grads/RelevantDecoderGRU_grucell3: 303.7006 - grads/IrrelevantDecoderGRU_grucell4: 203.3547 - grads/RelevantFactorsDense: 86.0689 - grads/IrrelevantFactorsDense: 45.6479 - grads/SynchronousBehaviouralDense: 7.1701 - grads/NeuralDense: 125.5040 - norms/EncoderGRUForward_grucell2: 1581.9101 - norms/EncoderGRUBackward_grucell1: 1576.2432 - norms/EncoderDense: 5950.7000 - norms/Releva

5/5 [==============================] - 1s 228ms/step - loss: 1956.9268 - loss/neural: 764.2478 - loss/behavioural: 1194.8969 - loss/relevant_kldiv: 61.4037 - loss/irrelevant_kldiv: 59.3671 - loss/reg: 1936.5994 - weights/neural_loglike: 1.0000 - weights/behavioural_loglike: 1.0000 - weights/relevant_kldiv: 0.0000e+00 - weights/irrelevant_kldiv: 0.0000e+00 - weights/reg: 0.0256 - learning_rate: 0.0100 - grads/EncoderGRUForward_grucell2: 640.6462 - grads/EncoderGRUBackward_grucell1: 663.1656 - grads/EncoderDense: 137649.9557 - grads/RelevantDenseMean: 1218.1860 - grads/IrrelevantDenseMean: 685.4124 - grads/RelevantDecoderGRU_grucell3: 14912.6932 - grads/IrrelevantDecoderGRU_grucell4: 7571.6103 - grads/RelevantFactorsDense: 5565.7467 - grads/IrrelevantFactorsDense: 2004.1370 - grads/SynchronousBehaviouralDense: 1099.3920 - grads/NeuralDense: 12985.2188 - norms/EncoderGRUForward_grucell2: 34321.4886 - norms/EncoderGRUBackward_grucell1: 34198.8558 - norms/EncoderDense: 129644.0638 - norms/R

5/5 [==============================] - 1s 219ms/step - loss: 1939.1703 - loss/neural: 750.4168 - loss/behavioural: 1216.6555 - loss/relevant_kldiv: 118.1753 - loss/irrelevant_kldiv: 103.7394 - loss/reg: 1907.1665 - weights/neural_loglike: 1.0000 - weights/behavioural_loglike: 1.0000 - weights/relevant_kldiv: 0.0000e+00 - weights/irrelevant_kldiv: 0.0000e+00 - weights/reg: 0.0506 - learning_rate: 0.0100 - grads/EncoderGRUForward_grucell2: 1450.0079 - grads/EncoderGRUBackward_grucell1: 1515.8063 - grads/EncoderDense: 268411.8802 - grads/RelevantDenseMean: 3857.2340 - grads/IrrelevantDenseMean: 2476.9281 - grads/RelevantDecoderGRU_grucell3: 29632.7155 - grads/IrrelevantDecoderGRU_grucell4: 15703.9038 - grads/RelevantFactorsDense: 12892.1004 - grads/IrrelevantFactorsDense: 4603.5303 - grads/SynchronousBehaviouralDense: 2821.9410 - grads/NeuralDense: 19718.7591 - norms/EncoderGRUForward_grucell2: 67081.3223 - norms/EncoderGRUBackward_grucell1: 66845.6673 - norms/EncoderDense: 257073.5104 - 

5/5 [==============================] - 1s 211ms/step - loss: 1938.9642 - loss/neural: 745.0215 - loss/behavioural: 1223.4925 - loss/relevant_kldiv: 147.0429 - loss/irrelevant_kldiv: 134.6356 - loss/reg: 1832.5037 - weights/neural_loglike: 1.0000 - weights/behavioural_loglike: 1.0000 - weights/relevant_kldiv: 0.0000e+00 - weights/irrelevant_kldiv: 0.0000e+00 - weights/reg: 0.0756 - learning_rate: 0.0095 - grads/EncoderGRUForward_grucell2: 2156.8162 - grads/EncoderGRUBackward_grucell1: 2271.0465 - grads/EncoderDense: 353502.5781 - grads/RelevantDenseMean: 5951.5514 - grads/IrrelevantDenseMean: 3853.1022 - grads/RelevantDecoderGRU_grucell3: 42938.5690 - grads/IrrelevantDecoderGRU_grucell4: 24496.2969 - grads/RelevantFactorsDense: 19998.4481 - grads/IrrelevantFactorsDense: 7735.7262 - grads/SynchronousBehaviouralDense: 4398.6213 - grads/NeuralDense: 25341.0806 - norms/EncoderGRUForward_grucell2: 99870.5807 - norms/EncoderGRUBackward_grucell1: 99523.0677 - norms/EncoderDense: 389430.5260 - 

...

5/5 [==============================] - 1s 239ms/step - loss: 1423.7600 - loss/neural: 698.8262 - loss/behavioural: 587.1307 - loss/relevant_kldiv: 70.6285 - loss/irrelevant_kldiv: 49.0525 - loss/reg: 825.4455 - weights/neural_loglike: 1.0000 - weights/behavioural_loglike: 1.0000 - weights/relevant_kldiv: 1.0000 - weights/irrelevant_kldiv: 1.0000 - weights/reg: 1.0000 - learning_rate: 1.4160e-04 - grads/EncoderGRUForward_grucell2: 1754449.3125 - grads/EncoderGRUBackward_grucell1: 1933941.1458 - grads/EncoderDense: 30957530.0000 - grads/RelevantDenseMean: 2248601.1667 - grads/IrrelevantDenseMean: 199773.1068 - grads/RelevantDecoderGRU_grucell3: 9842623.2500 - grads/IrrelevantDecoderGRU_grucell4: 916506.8646 - grads/RelevantFactorsDense: 1883818.0833 - grads/IrrelevantFactorsDense: 170213.7370 - grads/SynchronousBehaviouralDense: 37970.8506 - grads/NeuralDense: 250174.7786 - norms/EncoderGRUForward_grucell2: 3129331.5833 - norms/EncoderGRUBackward_grucell1: 3274511.4167 - norms/EncoderDen

5/5 [==============================] - 1s 212ms/step - loss: 1429.5775 - loss/neural: 698.1350 - loss/behavioural: 591.1233 - loss/relevant_kldiv: 70.2646 - loss/irrelevant_kldiv: 48.9618 - loss/reg: 824.8796 - weights/neural_loglike: 1.0000 - weights/behavioural_loglike: 1.0000 - weights/relevant_kldiv: 1.0000 - weights/irrelevant_kldiv: 1.0000 - weights/reg: 1.0000 - learning_rate: 1.3452e-04 - grads/EncoderGRUForward_grucell2: 1773013.1250 - grads/EncoderGRUBackward_grucell1: 1953894.3542 - grads/EncoderDense: 31289593.6667 - grads/RelevantDenseMean: 2274638.6458 - grads/IrrelevantDenseMean: 201779.1810 - grads/RelevantDecoderGRU_grucell3: 9971100.9167 - grads/IrrelevantDecoderGRU_grucell4: 930036.6979 - grads/RelevantFactorsDense: 1903660.3750 - grads/IrrelevantFactorsDense: 172117.6042 - grads/SynchronousBehaviouralDense: 38158.0238 - grads/NeuralDense: 252470.7083 - norms/EncoderGRUForward_grucell2: 3160870.9375 - norms/EncoderGRUBackward_grucell1: 3307997.1250 - norms/EncoderDen

5/5 [==============================] - 1s 217ms/step - loss: 1426.4784 - loss/neural: 703.4711 - loss/behavioural: 590.6937 - loss/relevant_kldiv: 69.4209 - loss/irrelevant_kldiv: 48.9024 - loss/reg: 823.9687 - weights/neural_loglike: 1.0000 - weights/behavioural_loglike: 1.0000 - weights/relevant_kldiv: 1.0000 - weights/irrelevant_kldiv: 1.0000 - weights/reg: 1.0000 - learning_rate: 1.2779e-04 - grads/EncoderGRUForward_grucell2: 1791279.1042 - grads/EncoderGRUBackward_grucell1: 1973545.5208 - grads/EncoderDense: 31621266.3333 - grads/RelevantDenseMean: 2300389.2083 - grads/IrrelevantDenseMean: 204127.1029 - grads/RelevantDecoderGRU_grucell3: 10100997.5833 - grads/IrrelevantDecoderGRU_grucell4: 947481.4688 - grads/RelevantFactorsDense: 1924002.1042 - grads/IrrelevantFactorsDense: 174386.8750 - grads/SynchronousBehaviouralDense: 38393.6859 - grads/NeuralDense: 255186.3411 - norms/EncoderGRUForward_grucell2: 3192407.0417 - norms/EncoderGRUBackward_grucell1: 3341477.6042 - norms/EncoderDe

5/5 [==============================] - 1s 215ms/step - loss: 1426.1929 - loss/neural: 699.6150 - loss/behavioural: 588.4568 - loss/relevant_kldiv: 69.8125 - loss/irrelevant_kldiv: 48.9956 - loss/reg: 823.2647 - weights/neural_loglike: 1.0000 - weights/behavioural_loglike: 1.0000 - weights/relevant_kldiv: 1.0000 - weights/irrelevant_kldiv: 1.0000 - weights/reg: 1.0000 - learning_rate: 1.2140e-04 - grads/EncoderGRUForward_grucell2: 1809112.2292 - grads/EncoderGRUBackward_grucell1: 1992880.7292 - grads/EncoderDense: 31956009.3333 - grads/RelevantDenseMean: 2326653.8750 - grads/IrrelevantDenseMean: 206368.2240 - grads/RelevantDecoderGRU_grucell3: 10234198.8333 - grads/IrrelevantDecoderGRU_grucell4: 961730.1771 - grads/RelevantFactorsDense: 1943647.0833 - grads/IrrelevantFactorsDense: 176275.6107 - grads/SynchronousBehaviouralDense: 38625.6699 - grads/NeuralDense: 257625.6484 - norms/EncoderGRUForward_grucell2: 3223936.9583 - norms/EncoderGRUBackward_grucell1: 3374952.0625 - norms/EncoderDe

5/5 [==============================] - 1s 220ms/step - loss: 1422.3002 - loss/neural: 704.4062 - loss/behavioural: 584.0120 - loss/relevant_kldiv: 69.0386 - loss/irrelevant_kldiv: 48.8208 - loss/reg: 822.6240 - weights/neural_loglike: 1.0000 - weights/behavioural_loglike: 1.0000 - weights/relevant_kldiv: 1.0000 - weights/irrelevant_kldiv: 1.0000 - weights/reg: 1.0000 - learning_rate: 1.1533e-04 - grads/EncoderGRUForward_grucell2: 1828065.0417 - grads/EncoderGRUBackward_grucell1: 2013248.8750 - grads/EncoderDense: 32312331.0000 - grads/RelevantDenseMean: 2354511.5208 - grads/IrrelevantDenseMean: 208709.3424 - grads/RelevantDecoderGRU_grucell3: 10369707.3333 - grads/IrrelevantDecoderGRU_grucell4: 975882.5208 - grads/RelevantFactorsDense: 1963533.3542 - grads/IrrelevantFactorsDense: 178310.1745 - grads/SynchronousBehaviouralDense: 38851.9124 - grads/NeuralDense: 260207.0938 - norms/EncoderGRUForward_grucell2: 3255464.8958 - norms/EncoderGRUBackward_grucell1: 3408423.5625 - norms/EncoderDe

In [6]:
import latentneural.plot as lnp
import numpy as np
import plotly.express as px
import plotly.graph_objects as go


log_f, b, _, _, _, _ = model(neural_data.astype('float'), training=False)
fig_rates = go.Figure(data=go.Heatmap(
    x=list(range(log_f.shape[1])), 
    y=list(range(log_f.shape[-1])), 
    z=np.exp(log_f[1, :, :].numpy().T), colorscale="Blues"))

fig_rates.update_layout(title='Firing Rates of Condition Trial #%d' % (0),
                xaxis_title='Time',
                yaxis_title='Neurons')

fig_rates_n = go.Figure(data=go.Heatmap(
    x=list(range(log_f.shape[1])), 
    y=list(range(log_f.shape[-1])), 
    z=dataset['train_rates'][1, :, :].T, colorscale="Blues"))

fig_rates_n.update_layout(title='Firing Rates of Condition Trial #%d' % (0),
                xaxis_title='Time',
                yaxis_title='Neurons')

fig_rates.show()
fig_rates_n.show()

In [7]:
log_f, b, (g0, mean, logvar), _, (z_r, z_i), _ = model(neural_data.astype('float'), training=False)

fig_z = go.Figure(data=go.Heatmap(
    x=list(range(log_f.shape[1])), 
    y=list(range(log_f.shape[-1])), 
    z=z_r.numpy()[0, :, :].T, colorscale="Blues"))

fig_z.update_layout(title='Latent Variables of Condition Trial #%d' % (0),
                xaxis_title='Time',
                yaxis_title='Neurons')

fig_z_n = go.Figure(data=go.Heatmap(
    x=list(range(log_f.shape[1])), 
    y=list(range(log_f.shape[-1])), 
    z=dataset['train_latent'][0, :, :].T, colorscale="Blues"))

fig_z_n.update_layout(title='Latent Variables of Condition Trial #%d' % (0),
                xaxis_title='Time',
                yaxis_title='Neurons')

fig_z.show()
fig_z_n.show()

In [8]:
latent_reconstructed_unsorted = np.concatenate([z_r.numpy().T, z_i.numpy().T], axis=0)
latent_original = dataset['train_latent'].T

print(latent_reconstructed_unsorted.shape)
print(latent_original.shape)

(3, 100, 70)
(3, 100, 70)


In [9]:
latent_reconstructed_unsorted_r = latent_reconstructed_unsorted.reshape(
    latent_reconstructed_unsorted.shape[0], 
    latent_reconstructed_unsorted.shape[1] * latent_reconstructed_unsorted.shape[2]).T

latent_original_r = latent_original.reshape(
    latent_original.shape[0], 
    latent_original.shape[1] * latent_original.shape[2]).T

In [10]:
from sklearn.linear_model import Ridge

clf = Ridge(alpha=1.0)
clf.fit(latent_reconstructed_unsorted_r, latent_original_r)
print('Score: ', clf.score(latent_reconstructed_unsorted_r, latent_original_r))

predictions = clf.predict(latent_reconstructed_unsorted_r).T.reshape(latent_original.shape[0], latent_reconstructed_unsorted.shape[1], latent_reconstructed_unsorted.shape[2])

Score:  0.7989150646220612


In [11]:
fig = go.Figure()
condition=0
for d in range(3):
    # Create and style traces
    fig.add_trace(go.Scatter(x=dataset['time_data'], y=latent_original[d,:,condition], name='%d original' % (d),
                            line=dict(color=px.colors.qualitative.Plotly[d], width=10), opacity=0.2))
    fig.add_trace(go.Scatter(x=dataset['time_data'], y=predictions[d,:,condition], name='%d reconstructed' % (d),
                            line = dict(color=px.colors.qualitative.Plotly[d], width=2)))

# Edit the layout
fig.update_layout(title='Latent Trajectories of Condition #%d, Original vs Reconstructed' % (condition),
                xaxis_title='Time',
                yaxis_title='Value')
fig.show()

# Vaidation Performance

In [12]:
log_f, b, (g0, mean, logvar), _, (z_r, z_i), _ = model(dataset['valid_data'].astype('float'), training=False)
latent_reconstructed_unsorted = np.concatenate([z_r.numpy().T, z_i.numpy().T], axis=0)
latent_original = dataset['valid_latent'].T
latent_reconstructed_unsorted_r = latent_reconstructed_unsorted.reshape(
    latent_reconstructed_unsorted.shape[0], latent_reconstructed_unsorted.shape[1] * latent_reconstructed_unsorted.shape[2]).T
latent_original_r = latent_original.reshape(
    latent_original.shape[0], latent_original.shape[1] * latent_original.shape[2]).T

clf = Ridge(alpha=1.0)
clf.fit(latent_reconstructed_unsorted_r, latent_original_r)
print('Score: ', clf.score(latent_reconstructed_unsorted_r, latent_original_r))

Score:  0.7916757411923551


# Behaviour Reconstruction

In [13]:
fig = go.Figure()
b_noiseless = dataset['valid_latent'][:,:,-dataset['behaviour_weights'].shape[0]:] @ \
    dataset['behaviour_weights'][:,:]
    
condition=0
for d in range(3):
    # Create and style traces
    fig.add_trace(go.Scatter(x=dataset['time_data'], y=b_noiseless[condition,:,d], name='%d original noisless' % (d),
                            line=dict(color=px.colors.qualitative.Plotly[d], width=10), opacity=0.2))
    fig.add_trace(go.Scatter(x=dataset['time_data'], y=b[condition,:,d], name='%d reconstructed' % (d),
                            line = dict(color=px.colors.qualitative.Plotly[d], width=2)))

# Edit the layout
fig.update_layout(title='Behavioural Trajectories of Condition #%d, Original vs Reconstructed' % (condition),
                xaxis_title='Time',
                yaxis_title='Value')
fig.show()